## Import Libraries

In [1]:
from genericpath import exists
import pdb
from pickletools import uint8
from turtle import pd
import torchvision
import torch
import os
import sys
sys.path.insert(0, '../')
#from models.model_mrcnn import _default_mrcnn_config, build_default
import torchvision
import torch
from models_pytorch_lightning.generalized_mask_rcnn_pl import LitMaskRCNN

# from torchknickknacks import modelutils
from PIL import Image
import matplotlib.pyplot as plt
from torchvision import transforms
from pytorch_grad_cam.utils.image import show_cam_on_image

import numpy as np
import cv2
import requests
import random
import glob
from skimage.measure import label, regionprops, regionprops_table
from skimage import data, filters, measure, morphology
import pandas as pd
import wandb
from tqdm import tqdm
from skimage import data
from skimage.color import rgb2hed, hed2rgb

In [2]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score
import plotly.graph_objects as go
from sklearn.metrics import roc_curve, auc
from sklearn.metrics import precision_recall_curve

## Utility Functions

In [3]:
class GetExternalDataOutput():
    
    # TODO fix the visualization flags
    def __init__(self, model, test_input_path, detection_threshold):
        self.model = model
        self.test_input_path = test_input_path
        self.detection_threshold = detection_threshold
        self.class_names = ['Cored', 'Diffuse', 'Coarse-Grained', 'CAA']
        self.class_to_colors = {'Cored': (255, 0, 0), 'Diffuse' : (0, 0, 255), 'Coarse-Grained': (0,255,0), 'CAA':(225, 255, 0)}
        #TODO change this to nas location later
        self.result_save_dir= "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/Results-Nature/"
        self.colors = np.random.uniform(0, 255, size=(len(self.class_names), 3))
    

    def get_outputs_nms(self, input_tensor, model, score_threshold = 0.5, iou_threshold = 0.5):
        #mask_list = []
        #label_list = []
        #score_list =[]
        #box_list = []
        with torch.no_grad():
            # forward pass of the image through the modle
            outputs = model(input_tensor)
        boxes = outputs[0]['boxes']
        labels = outputs[0]['labels']
        scores = outputs[0]['scores']
        masks = outputs[0]['masks']
        #print(boxes.shape,labels.shape, masks.shape)
        # Apply score threshold
        keep = scores > score_threshold
        boxes, labels, scores, masks = boxes[keep], labels[keep], scores[keep], masks[keep]
        #print(boxes.shape,labels.shape, masks.shape)
        #print(keep)
        keep = torchvision.ops.nms(boxes, scores, iou_threshold)
        boxes, labels, scores, masks = boxes[keep], labels[keep], scores[keep], masks[keep]
        #print(keep)
        #print(boxes.shape,labels.shape, masks.shape)
        scores = list(scores.detach().cpu().numpy())
        #print(scores)
        masks = list((masks>0.5).detach().cpu().numpy())
        #masks = list((masks>0.5).squeeze().detach().cpu().numpy())
        #print(masks.shape)
        boxes = [[(int(i[0]), int(i[1])), (int(i[2]), int(i[3]))]  for i in boxes.detach().cpu()]
        labels = list(labels.detach().cpu().numpy())
        labels = [self.class_names[i-1] for i in labels]
        return masks, boxes, labels, scores



    def prepare_input(self, image):
        image_float_np = np.float32(image) / 255
        # define the torchvision image transforms
        transform = torchvision.transforms.Compose([
            torchvision.transforms.Resize(1024),
            torchvision.transforms.ToTensor(),
        ])
        input_tensor = transform(transforms.ToPILImage()(image))
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        input_tensor = input_tensor.to(device)
        # Add a batch dimension:
        input_tensor = input_tensor.unsqueeze(0)
        return input_tensor, image_float_np


    def generate_results(self):
        # This will help us create a different color for each class
        # Load Trained 
        
        #self.model.load_state_dict(torch.load(self.model_input_path))
    
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        
        self.model.eval().to(device)
        output_dict=dict()
        output_score=dict()
        

        test_folders = glob.glob(os.path.join(self.test_input_path, "*"))
        
        # Test images from each WSI folder
        test_folders = sorted(test_folders)
        
        print("length of test folders", len(test_folders))
        
        output_dict = dict()
      
        for test_folder in tqdm(test_folders):

            print("\n", test_folder)
            
            folder_name = os.path.basename(test_folder)

            if folder_name == "labels":
                continue

            # make all necessary folders
            #self.make_result_dirs(folder_name)
            images = glob.glob(os.path.join(test_folder, '*.jpg'))
            
            print("Images in Test Folder", len(images))
            i = 0

            for img in tqdm(images):
                result_img = 0
                img_name = os.path.basename(img).split('.')[0]
                
                image = np.array(Image.open(img))

                #total_image_pixels+= image.shape[0] * image.shape[1]
                # Check if image has alpha channel
                if image.shape[2] == 4:
                    image = image[:,:, :3]
                input_tensor, image_float_np = self.prepare_input(image)

                masks, boxes, labels, scores = self.get_outputs_nms(input_tensor, self.model, 0.3, self.detection_threshold)
                #print(labels, scores)
                #print(labels)
                output_dict[img_name] = labels
                output_score[img_name]=scores
        return output_dict, output_score
    
    def generate_results_per_image(self):
        # This will help us create a different color for each class
        # Load Trained 
        output_dict=dict()
        output_score=dict()
        
        self.model.load_state_dict(torch.load(self.model_input_path))
    
        device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        self.model.eval().to(device)
        output_dict=dict()
        output_score=dict()
        test_folders = glob.glob(os.path.join("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB", "*.jpg"))
        print(len(test_folders))
        #for Finkbeiner-Steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB 
        for img in  test_folders:
            #img = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4751-02_AB/NA4751-02_AB_19_6_34.jpg"
            #img = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/amyb_wsi/train/images/A_0_0_XE10-045_1_AmyB_1_49175x_54069y_image.png"
            img_name = os.path.basename(img).split('.')[0]
            image = np.array(Image.open(img))

            #total_image_pixels+= image.shape[0] * image.shape[1]
            # Check if image has alpha channel
            if image.shape[2] == 4:
                image = image[:,:, :3]
            input_tensor, image_float_np = self.prepare_input(image)

            masks, boxes, labels, scores = self.get_outputs_nms(input_tensor, self.model, 0.5, self.detection_threshold)
            #print(labels, scores)
            #print(labels)
            output_dict[img_name] = labels
            output_score[img_name]=scores
        return output_dict, output_score


## Evaluate External Dataset

In [4]:
image_dataset =  "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/"

gt_train = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/classification_dataset/train.csv"

gt_val = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/validation.csv"

model_name = "/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/runpod_mrcnn_models/yp2mf3i8_epoch=108-step=872.ckpt"
model = LitMaskRCNN.load_from_checkpoint(model_name)

/home/mahirwar/miniconda3/envs/kfold_amy_plaque1/lib/python3.9/site-packages/lightning/pytorch/utilities/parsing.py:198: Attribute 'backbone' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['backbone'])`.
/home/mahirwar/miniconda3/envs/kfold_amy_plaque1/lib/python3.9/site-packages/lightning/pytorch/utilities/parsing.py:198: Attribute 'rpn' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['rpn'])`.
/home/mahirwar/miniconda3/envs/kfold_amy_plaque1/lib/python3.9/site-packages/lightning/pytorch/utilities/parsing.py:198: Attribute 'roi_heads' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['roi_heads'])`.
/home/mahirwar/miniconda3/envs/kfold_amy_plaque1/lib/python3.9/site-packages/lightning/pytorch/u

In [5]:
def evaluate_output(gt_train, output_df, output_score, train_flag):
    gt_train_df = pd.read_csv(gt_train)
    gt_train_df["imagename2"]= gt_train_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))
    if train_flag:
        gt_train_df["cored_gt"] = gt_train_df["cored_bool"].apply(lambda l: 1 if l==True else 0)
        gt_train_df["diffuse_gt"] = gt_train_df["diffuse_bool"].apply(lambda l: 1 if l==True else 0)
        gt_train_df["CAA_gt"] = gt_train_df["CAA_bool"].apply(lambda l: 1 if l==True else 0)
    else:
        gt_train_df["cored_gt"] = gt_train_df["cored"].apply(lambda l: 1 if l>0 else 0)
        gt_train_df["diffuse_gt"] = gt_train_df["diffuse"].apply(lambda l: 1 if l>0 else 0)
        gt_train_df["CAA_gt"] = gt_train_df["CAA"].apply(lambda l: 1 if l>0 else 0)
        
    gt_train_df["cored_pred"] = 0
    gt_train_df["diffuse_pred"] = 0
    gt_train_df["CAA_pred"] = 0
    
    def assign_pred_scores(row, val):
        if row["imagename2"] in output_df.keys():
            l = output_df[row["imagename2"]]
            s = output_score[row["imagename2"]]
            indices = [i for i in range(len(l)) if l[i] == val]
            s_selected = [ s[i] for i in indices]
            if len(s_selected)!=0:
                return max(s_selected)
            else:
                return 0
        else:
            return None
    
    gt_train_df["cored_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Cored"), axis=1)
    gt_train_df["diffuse_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Diffuse"),axis=1)
    gt_train_df["cg_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "Coarse-Grained"),axis=1)
    gt_train_df["CAA_score"] = gt_train_df.apply(lambda l:  assign_pred_scores(l, "CAA"),axis=1)
    
    def assign_pred_labels(row, val):
        if row["imagename2"] in output_df.keys():
            l = output_df[row["imagename2"]]
            if val in l:
                return 1
            else:
                return 0
        else:
            return None
    
    gt_train_df["cored_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Cored"), axis=1)
    gt_train_df["diffuse_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Diffuse"),axis=1)
    gt_train_df["cg_score"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "Coarse-Grained"),axis=1)
    gt_train_df["CAA_pred"] = gt_train_df.apply(lambda l:  assign_pred_labels(l, "CAA"),axis=1)
    return gt_train_df
    

In [6]:

explain = GetExternalDataOutput(model, test_input_path=image_dataset, detection_threshold=0.4)
output_df, output_scores = explain.generate_results()


length of test folders 29


  0%|          | 0/29 [00:00<?, ?it/s]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4009-02_AB
Images in Test Folder 3897


  3%|▎         | 1/29 [08:33<3:59:25, 513.06s/it]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA4072-02_AB
Images in Test Folder 344


...

 93%|█████████▎| 27/29 [2:06:03<04:19, 129.83s/it]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA_4883_02_AB
Images in Test Folder 253


 97%|█████████▋| 28/29 [2:06:37<01:41, 101.11s/it]


 /gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/tiles/train/NA_4888_02_AB17-24
Images in Test Folder 3675


100%|██████████| 29/29 [2:14:42<00:00, 278.70s/it]


In [7]:
output_df


{'NA4009-02_AB_22_21_50': ['Coarse-Grained'],
 'NA4009-02_AB_10_27_31': ['Diffuse', 'CAA', 'CAA'],
 'NA4009-02_AB_10_21_74': ['Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse',
  'Diffuse'],
 'NA4009-02_AB_7_16_12': [],
 'NA4009-02_AB_8_4_2': ['Diffuse'],
 'NA4009-02_AB_20_11_25': ['Diffuse'],
 'NA4009-02_AB_26_16_34': ['Diffuse'],
 'neg_NA4009-02_AB_5_21_2': [],
 'NA4009-02_AB_23_16_4': ['Diffuse'],
 'NA4009-02_AB_15_20_10': [],
 'NA4009-02_AB_5_29_26': [],
 'NA4009-02_AB_6_26_62': ['Coarse-Grained', 'Coarse-Grained'],
 'NA4009-02_AB_6_28_54': ['Diffuse'],
 'NA4009-02_AB_17_6_71': ['Diffuse'],
 'NA4009-02_AB_6_21_22': ['Diffuse', 'Diffuse', 'Diffuse', 'CAA'],
 'NA4009-02_AB_15_35_15': ['Diffuse'],
 'NA4009-02_AB_24_22_27': [],
 'neg_NA4009-02_AB_13_19_3': [],
 'NA4009-02_AB_6_28_10': ['CAA', 'Diffuse'],
 'NA4009-02_AB_7_10_65': ['CAA', 'CAA'],
 'neg_NA4009-02_AB_6_35_4': [],
 'NA4009-02_AB_28_33_16': ['Diffuse'],
 'NA4009-02_AB_9_19_6': ['Diffuse'],
 'NA4009-02_AB_6_20_2':

In [8]:
output_scores

{'NA4009-02_AB_22_21_50': [0.77416444],
 'NA4009-02_AB_10_27_31': [0.86789554, 0.8321429, 0.8238295],
 'NA4009-02_AB_10_21_74': [0.9111257,
  0.7572885,
  0.72732615,
  0.6137131,
  0.5296569,
  0.32546493],
 'NA4009-02_AB_7_16_12': [],
 'NA4009-02_AB_8_4_2': [0.9025852],
 'NA4009-02_AB_20_11_25': [0.7187162],
 'NA4009-02_AB_26_16_34': [0.96922016],
 'neg_NA4009-02_AB_5_21_2': [],
 'NA4009-02_AB_23_16_4': [0.77968335],
 'NA4009-02_AB_15_20_10': [],
 'NA4009-02_AB_5_29_26': [],
 'NA4009-02_AB_6_26_62': [0.8132504, 0.65848386],
 'NA4009-02_AB_6_28_54': [0.6911069],
 'NA4009-02_AB_17_6_71': [0.40255526],
 'NA4009-02_AB_6_21_22': [0.8727435, 0.85925335, 0.81067234, 0.72591937],
 'NA4009-02_AB_15_35_15': [0.65485454],
 'NA4009-02_AB_24_22_27': [],
 'neg_NA4009-02_AB_13_19_3': [],
 'NA4009-02_AB_6_28_10': [0.9072429, 0.8151504],
 'NA4009-02_AB_7_10_65': [0.98147935, 0.32454327],
 'neg_NA4009-02_AB_6_35_4': [],
 'NA4009-02_AB_28_33_16': [0.9028534],
 'NA4009-02_AB_9_19_6': [0.95370555],
 'NA4

In [9]:
model_output_df = pd.DataFrame(columns=["imagename2","label_pred","score_pred"])
for k,v in output_df.items():
    for j in range(len(v)):
        model_output_df.loc[len(model_output_df)] = [k, v[j], output_scores[k][j]]

In [10]:
model_output_df

imagename2      label_pred  score_pred
0          NA4009-02_AB_22_21_50  Coarse-Grained    0.774164
1          NA4009-02_AB_10_27_31         Diffuse    0.867896
2          NA4009-02_AB_10_27_31             CAA    0.832143
3          NA4009-02_AB_10_27_31             CAA    0.823829
4          NA4009-02_AB_10_21_74         Diffuse    0.911126
...                          ...             ...         ...
87724  NA_4888_02_AB17-24_8_15_4         Diffuse    0.919301
87725  NA_4888_02_AB17-24_8_15_4         Diffuse    0.904309
87726  NA_4888_02_AB17-24_8_15_4         Diffuse    0.887495
87727  NA_4888_02_AB17-24_8_15_4         Diffuse    0.518984
87728  NA_4888_02_AB17-24_7_14_1         Diffuse    0.547963

[87729 rows x 3 columns]

In [11]:
gt_train_df = pd.read_csv(gt_train)
gt_train_df["imagename2"]= gt_train_df["imagename"].apply(lambda l: l.split("/")[-1].replace(".jpg",""))

In [12]:
model_output_df1 = pd.merge(model_output_df, gt_train_df[["imagename","imagename2"]], how="left", on="imagename2")

In [13]:
model_output_df1["folder_name"] = model_output_df1["imagename"].apply(lambda l: str(l).split("/")[0])

In [79]:
model_output_df1[model_output_df1["folder_name"]=="NA4009-02_AB"]

imagename2      label_pred  score_pred  \
0     NA4009-02_AB_22_21_50  Coarse-Grained    0.774164   
1     NA4009-02_AB_10_27_31         Diffuse    0.867896   
2     NA4009-02_AB_10_27_31             CAA    0.832143   
3     NA4009-02_AB_10_27_31             CAA    0.823829   
4     NA4009-02_AB_10_21_74         Diffuse    0.911126   
...                     ...             ...         ...   
5769  NA4009-02_AB_21_35_42         Diffuse    0.805553   
5770  NA4009-02_AB_21_35_42         Diffuse    0.747272   
5771  NA4009-02_AB_21_35_42         Diffuse    0.566200   
5772  NA4009-02_AB_21_35_42         Diffuse    0.547035   
5773  NA4009-02_AB_23_34_15         Diffuse    0.979649   

                                   imagename   folder_name  
0     NA4009-02_AB/NA4009-02_AB_22_21_50.jpg  NA4009-02_AB  
1     NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
2     NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
3     NA4009-02_AB/NA4009-02_AB_10_27_31.jpg  NA4009-02_AB  
4     NA4009-02_AB/NA4009-02_AB_10_21_74.jpg  NA4009-02_AB  
...                                      ...           ...  
5769  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
5770  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
5771  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
5772  NA4009-02_AB/NA4009-02_AB_21_35_42.jpg  NA4009-02_AB  
5773  NA4009-02_AB/NA4009-02_AB_23_34_15.jpg  NA4009-02_AB  

[5764 rows x 5 columns]

In [14]:
# running validation dataset
gt_val_df = evaluate_output(gt_val, output_df, output_scores, False)

In [15]:
# running train dataset
gt_train_df = evaluate_output(gt_train, output_df, output_scores, False)

In [16]:
# excluding NA values from val
notna_gt_val_df = gt_val_df[~gt_val_df["cored_pred"].isna()]

In [17]:
# excluding NA values from train
notna_gt_train_df = gt_train_df[~gt_train_df["cored_pred"].isna()]

In [18]:
# dropping irrelevant columns from train
notna_gt_train_df.drop(['Unnamed: 0',"cored_bool","diffuse_bool","CAA_bool"], axis=1, inplace=True)

/tmp/ipykernel_2705533/4151113692.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  notna_gt_train_df.drop(['Unnamed: 0',"cored_bool","diffuse_bool","CAA_bool"], axis=1, inplace=True)


In [19]:
# Concatenate train and val outputs
final_df = pd.concat([notna_gt_train_df,notna_gt_val_df], ignore_index=True)

In [20]:
final_df

id                                        imagename  cored  \
0       10748           NA4757-02_AB/NA4757-02_AB_18_25_61.jpg    1.0   
1       29503  NA4918-02_AB17-24/NA4918-02_AB17-24_9_18_12.jpg    0.0   
2       42524  NA4885-02_AB17-24/NA4885-02_AB17-24_4_23_50.jpg    1.0   
3       34432           NA4749-02_AB/NA4749-02_AB_17_12_50.jpg    0.0   
4        4137            NA4751-02_AB/NA4751-02_AB_19_6_34.jpg    0.0   
...       ...                                              ...    ...   
151991   9606             NA4751-02_AB/NA4751-02_AB_14_0_9.jpg    0.0   
151992   1137  NA4918-02_AB17-24/NA4918-02_AB17-24_14_1_48.jpg    1.0   
151993   9972                 NA5001_2AB/NA5001_2AB_16_2_2.jpg    0.0   
151994   7975            NA4751-02_AB/NA4751-02_AB_3_31_11.jpg    0.0   
151995  10523           NA4722-02_AB/NA4722-02_AB_21_28_13.jpg    0.0   

         diffuse      CAA  negative     flag  notsure  \
0       0.000000  0.00000   0.00000  0.00000  0.00000   
1       2.832462  0.00000   0.00000  0.00000  0.00000   
2       1.000000  0.00000   0.00000  1.00000  0.00000   
3       3.770270  0.00000   0.00000  0.00000  0.00000   
4       1.000000  2.00000   0.00000  2.00000  0.00000   
...          ...      ...       ...      ...      ...   
151991  0.000000  1.00000   0.00000  1.00000  0.00000   
151992  1.136264  0.00000   0.00000  0.00000  0.00000   
151993  1.000000  1.00000   0.00000  1.00000  0.00000   
151994  0.000000  1.00000   1.23913  0.00000  1.23913   
151995  0.000000  2.03825   0.00000  2.03825  0.00000   

                       imagename2  cored_gt  diffuse_gt  CAA_gt  cored_pred  \
0           NA4757-02_AB_18_25_61         1           0       0         0.0   
1       NA4918-02_AB17-24_9_18_12         0           1       0         0.0   
2       NA4885-02_AB17-24_4_23_50         1           1       0         0.0   
3           NA4749-02_AB_17_12_50         0           1       0         0.0   
4            NA4751-02_AB_19_6_34         0           1       1         0.0   
...                           ...       ...         ...     ...         ...   
151991        NA4751-02_AB_14_0_9         0           0       1         0.0   
151992  NA4918-02_AB17-24_14_1_48         1           1       0         0.0   
151993          NA5001_2AB_16_2_2         0           1       1         0.0   
151994       NA4751-02_AB_3_31_11         0           0       1         0.0   
151995      NA4722-02_AB_21_28_13         0           0       1         0.0   

        diffuse_pred  CAA_pred  cored_score  diffuse_score  cg_score  \
0                0.0       1.0          0.0       0.000000       0.0   
1                1.0       0.0          0.0       0.981835       0.0   
2                0.0       1.0          0.0       0.000000       0.0   
3                1.0       0.0          0.0       0.786405       0.0   
4                0.0       1.0          0.0       0.000000       0.0   
...              ...       ...          ...            ...       ...   
151991           0.0       1.0          0.0       0.000000       0.0   
151992           1.0       1.0          0.0       0.891719       0.0   
151993           0.0       1.0          0.0       0.000000       0.0   
151994           0.0       0.0          0.0       0.000000       0.0   
151995           0.0       1.0          0.0       0.000000       0.0   

        CAA_score  
0        0.964038  
1        0.000000  
2        0.959290  
3        0.000000  
4        0.995171  
...           ...  
151991   0.912814  
151992   0.836158  
151993   0.854183  
151994   0.000000  
151995   0.993077  

[151996 rows x 19 columns]

In [65]:
final_df =  pd.read_csv("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/classification_dataset/final_output_train_val_nature.csv")

In [66]:
final_df.head(2)

Unnamed: 0     id                                        imagename  cored  \
0           0  10748           NA4757-02_AB/NA4757-02_AB_18_25_61.jpg    1.0   
1           1  29503  NA4918-02_AB17-24/NA4918-02_AB17-24_9_18_12.jpg    0.0   

    diffuse  CAA  negative  flag  notsure                 imagename2  \
0  0.000000  0.0       0.0   0.0      0.0      NA4757-02_AB_18_25_61   
1  2.832462  0.0       0.0   0.0      0.0  NA4918-02_AB17-24_9_18_12   

   cored_gt  diffuse_gt  CAA_gt  cored_pred  diffuse_pred  CAA_pred  \
0         1           0       0         0.0           0.0       1.0   
1         0           1       0         0.0           1.0       0.0   

   cored_score  diffuse_score  cg_score  CAA_score  
0          0.0       0.000000       0.0   0.964038  
1          0.0       0.981835       0.0   0.000000

In [30]:
final_df["cored_pred"] = np.where(final_df["cored_score"]>0.6, 1, 0)
final_df["diffuse_pred"] = np.where(final_df["diffuse_score"]>0.6, 1, 0)
final_df["CAA_pred"] = np.where(final_df["CAA_score"]>0.6, 1, 0)

In [31]:
tmp = final_df[["cored_gt","diffuse_gt","CAA_gt","cored_pred","diffuse_pred","CAA_pred"]].drop_duplicates()

In [32]:
len(tmp)

50

## Classification Metric - Core

In [21]:
#tmp =  final_df[final_df["cored_gt"]>0]
#print(len(tmp))
#print(classification_report(tmp["cored_gt"], tmp["cored_pred"]))
print(classification_report(final_df["cored_gt"], final_df["cored_pred"]))#

              precision    recall  f1-score   support

           0       0.73      0.97      0.84    101571
           1       0.84      0.29      0.43     50425

    accuracy                           0.75    151996
   macro avg       0.79      0.63      0.63    151996
weighted avg       0.77      0.75      0.70    151996



In [22]:
tmp = final_df[final_df["cored_gt"]!=final_df["cored_pred"]]
len(tmp[tmp["CAA_score"]>0.80])

19170

In [23]:
final_df[(final_df["CAA_gt"]>0) & (final_df["CAA_pred"]<=0)]

id                               imagename  cored   diffuse  \
5        4525        NA5001_2AB/NA5001_2AB_16_6_5.jpg    0.0  0.000000   
23       4339        NA5001_2AB/NA5001_2AB_2_17_5.jpg    0.0  0.000000   
29      36583        NA5001_2AB/NA5001_2AB_6_21_3.jpg    0.0  0.000000   
35      38277        NA5001_2AB/NA5001_2AB_9_16_0.jpg    0.0  0.000000   
38       3826      NA5001_2AB/NA5001_2AB_20_16_17.jpg    0.0  2.355932   
...       ...                                     ...    ...       ...   
151975   9267        NA5003_2AB/NA5003_2AB_5_15_2.jpg    0.0  0.000000   
151985   9993  NA4619-02_AB/NA4619-02_AB_22_25_17.jpg    0.0  0.000000   
151988   3561       NA5003_2AB/NA5003_2AB_6_31_36.jpg    0.0  0.000000   
151990    129         NA5001_2AB/NA5001_2AB_9_8_8.jpg    0.0  1.235669   
151994   7975   NA4751-02_AB/NA4751-02_AB_3_31_11.jpg    0.0  0.000000   

             CAA  negative      flag  notsure             imagename2  \
5       1.000000   0.00000  0.000000  0.00000      NA5001_2AB_16_6_5   
23      1.439024   0.00000  1.000000  0.00000      NA5001_2AB_2_17_5   
29      1.000000   1.00000  0.000000  0.00000      NA5001_2AB_6_21_3   
35      1.000000   0.00000  1.000000  0.00000      NA5001_2AB_9_16_0   
38      1.000000   0.00000  2.000000  0.00000    NA5001_2AB_20_16_17   
...          ...       ...       ...      ...                    ...   
151975  1.000000   1.25000  1.000000  0.00000      NA5003_2AB_5_15_2   
151985  1.780000   0.00000  1.780000  0.00000  NA4619-02_AB_22_25_17   
151988  2.357143   0.00000  2.357143  0.00000     NA5003_2AB_6_31_36   
151990  1.010251   0.00000  1.010251  0.00000       NA5001_2AB_9_8_8   
151994  1.000000   1.23913  0.000000  1.23913   NA4751-02_AB_3_31_11   

        cored_gt  diffuse_gt  CAA_gt  cored_pred  diffuse_pred  CAA_pred  \
5              0           0       1         0.0           0.0       0.0   
23             0           0       1         0.0           0.0       0.0   
29             0           0       1         0.0           0.0       0.0   
35             0           0       1         0.0           0.0       0.0   
38             0           1       1         0.0           1.0       0.0   
...          ...         ...     ...         ...           ...       ...   
151975         0           0       1         0.0           0.0       0.0   
151985         0           0       1         0.0           0.0       0.0   
151988         0           0       1         0.0           0.0       0.0   
151990         0           1       1         0.0           1.0       0.0   
151994         0           0       1         0.0           0.0       0.0   

        cored_score  diffuse_score  cg_score  CAA_score  
5               0.0       0.000000       0.0        0.0  
23              0.0       0.000000       0.0        0.0  
29              0.0       0.000000       0.0        0.0  
35              0.0       0.000000       0.0        0.0  
38              0.0       0.671855       1.0        0.0  
...             ...            ...       ...        ...  
151975          0.0       0.000000       0.0        0.0  
151985          0.0       0.000000       0.0        0.0  
151988          0.0       0.000000       0.0        0.0  
151990          0.0       0.492020       0.0        0.0  
151994          0.0       0.000000       0.0        0.0  

[27959 rows x 19 columns]

## Classification Metric - Diffuse

In [24]:
print(classification_report(final_df["diffuse_gt"], final_df["diffuse_pred"]))

              precision    recall  f1-score   support

           0       0.64      0.81      0.72     72939
           1       0.77      0.59      0.67     79057

    accuracy                           0.69    151996
   macro avg       0.71      0.70      0.69    151996
weighted avg       0.71      0.69      0.69    151996



## Classification Metric - CAA

In [25]:
print(classification_report(final_df["CAA_gt"], final_df["CAA_pred"]))

              precision    recall  f1-score   support

           0       0.69      0.61      0.65    102229
           1       0.36      0.44      0.39     49767

    accuracy                           0.56    151996
   macro avg       0.52      0.53      0.52    151996
weighted avg       0.58      0.56      0.57    151996



In [71]:
final_df.to_csv("/gladstone/finkbeiner/steve/work/data/npsad_data/vivek/Datasets/UCDavis-Dataset/classification_dataset/final_output_train_val_nature.csv")

## ROC Curve

In [26]:
import plotly.graph_objects as go
from sklearn.metrics import roc_curve, auc


colors={"cored":'royalblue', "diffuse":'firebrick','CAA':"green"}
df = final_df

fig = go.Figure()
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

for class_name in ["cored","diffuse","CAA"]:
    fpr, tpr, _ = roc_curve(df[class_name + "_gt"], df[class_name+"_score"])
    fig.add_trace(go.Scatter(x=fpr, y=tpr, name=class_name, mode='lines',line=dict(color=colors[class_name], width=2)))

fig.update_layout(
    xaxis_title='False Positive Rate',
    yaxis_title='True Positive Rate',
    yaxis=dict(scaleanchor="x", scaleratio=1),
    xaxis=dict(constrain='domain'),
    width=700, height=700
)
fig.update_layout( plot_bgcolor='white', title="Receiver operating characteristic Curve")
fig.update_xaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.update_yaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.show()
#fig.write_html("ROC_Curve.html")

## Precision Recall Curve

In [27]:
df = final_df

fig = go.Figure()
colors={"cored":'royalblue', "diffuse":'firebrick','CAA':"green"}
for class_name in ["cored","diffuse","CAA"]:
    pr, rc, _ = precision_recall_curve(df[class_name + "_gt"], df[class_name+"_score"])
    rp = (df[class_name + "_gt"]).sum()/len(df)
    fig.add_trace(go.Scatter(x=rc, y=pr, name=class_name, mode='lines',line=dict(color=colors[class_name], width=2)))
    #fig.add_trace(go.Scatter(x=[0,1], y=[rp,rp], name=class_name+"_random", mode='lines',line=dict(color=colors[class_name], width=2,dash='dash')))
    #fig.add_shape(type='line', line=dict(dash='dash',color=colors[class_name]), x0=0, x1=1, y0=rp, y1=rp, name=class_name)

fig.update_layout(
    xaxis_title='Recall',
    yaxis_title='Precision',
    yaxis=dict(scaleanchor="x", scaleratio=1),
    xaxis=dict(constrain='domain'),
    width=700, height=700
)
fig.update_layout( plot_bgcolor='white',title="Precision-Recall Curve")
fig.update_xaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.update_yaxes(mirror=True, ticks='outside', showline=True, linecolor='black',gridcolor='lightgrey')
fig.show()
#fig.write_html("PR_Curve.html")

In [ ]:
[[0.51735016 0.37484197 0.30489074 0.18063315]
 [0.50984456 0.37428932 0.29918033 0.17668488]
 [0.51518325 0.37699681 0.30584551 0.18130841]
 [0.5448505  0.4113968  0.34844869 0.2127193 ]
 [0.57629108 0.44122024 0.40136986 0.27247191]
 [0.60295931 0.4529549  0.42898975 0.29721362]
 [0.63540291 0.48044463 0.46581876 0.33684211]
 [0.67559944 0.4915754  0.4991453  0.36641221]
 [0.69075145 0.50064739 0.5026178  0.40506329]
 [0.73271889 0.51442521 0.52757353 0.44239631]
 [0.78512397 0.52322404 0.56015779 0.52459016]
 [0.7996633  0.53534884 0.57464213 0.53932584]
 [0.82229965 0.54437589 0.59787234 0.5748503 ]
 [0.83807829 0.55137482 0.61269147 0.60377358]
 [0.85923218 0.55883801 0.61640798 0.63157895]
 [0.86876155 0.56148148 0.62696629 0.6442953 ]
 [0.88593156 0.56580259 0.6369863  0.67132867]
 [0.8957529  0.5735146  0.64335664 0.70588235]
 [0.90335306 0.57684426 0.6507177  0.70588235]
 [0.90836653 0.58087855 0.6495098  0.70588235]
 [0.91836735 0.58617077 0.65346535 0.71641791]
 [0.92008197 0.59184754 0.66331658 0.71641791]
 [0.92307692 0.59636946 0.66496164 0.73282443]
 [0.92468619 0.60324324 0.66752577 0.73846154]
 [0.92210526 0.60862445 0.67447917 0.76190476]
 [0.92016807 0.61129386 0.68601583 0.74418605]
 [0.92781316 0.621802   0.69105691 0.768     ]
 [0.92144374 0.62107623 0.69589041 0.77419355]
 [0.92521368 0.62784091 0.69230769 0.77419355]
 [0.93304536 0.64124783 0.70985915 0.8       ]
 [0.93913043 0.64781341 0.71022727 0.80672269]
 [0.93873085 0.65582496 0.71387283 0.81355932]
 [0.94065934 0.65656566 0.71428571 0.82758621]
 [0.95100223 0.66526189 0.72403561 0.80672269]
 [0.95302013 0.6756591  0.73700306 0.85714286]
 [0.95720721 0.68533669 0.74143302 0.85714286]
 [0.95720721 0.68860759 0.74132492 0.85714286]
 [0.95918367 0.70298314 0.75080906 0.86486486]
 [0.96073903 0.71372032 0.77702703 0.87272727]
 [0.96690307 0.72255892 0.78596491 0.86486486]
 [0.97115385 0.73416841 0.79636364 0.85714286]
 [0.97080292 0.7514245  0.82129278 0.85714286]
 [0.97263682 0.76260044 0.82539683 0.87272727]
 [0.97236181 0.77241899 0.83884298 0.87272727]
 [0.9742268  0.79874214 0.85714286 0.87272727]
 [0.98167539 0.81382114 0.87155963 0.88073394]
 [0.98373984 0.8270361  0.89847716 0.88679245]
 [0.9833795  0.84995587 0.91463415 0.87735849]
 [0.98159509 0.87109005 0.96694215 0.88571429]
 [0.97785978 0.90065502 0.984375   0.9009901 ]]
[[0.98993964 0.94501992 0.97019868 0.89814815]
 [0.98993964 0.94422311 0.96688742 0.89814815]
 [0.98993964 0.94023904 0.97019868 0.89814815]
 [0.98993964 0.94342629 0.96688742 0.89814815]
 [0.98792757 0.94501992 0.97019868 0.89814815]
 [0.98390342 0.92828685 0.97019868 0.88888889]
 [0.96780684 0.92988048 0.97019868 0.88888889]
 [0.9637827  0.92988048 0.96688742 0.88888889]
 [0.96177062 0.92430279 0.95364238 0.88888889]
 [0.95975855 0.92350598 0.95033113 0.88888889]
 [0.95573441 0.91553785 0.94039735 0.88888889]
 [0.95573441 0.91713147 0.93046358 0.88888889]
 [0.94969819 0.91394422 0.93046358 0.88888889]
 [0.94768612 0.91075697 0.92715232 0.88888889]
 [0.94567404 0.90438247 0.9205298  0.88888889]
 [0.94567404 0.9059761  0.92384106 0.88888889]
 [0.93762575 0.90438247 0.92384106 0.88888889]
 [0.93360161 0.90756972 0.91390728 0.88888889]
 [0.92152918 0.89721116 0.90066225 0.88888889]
 [0.91750503 0.89561753 0.87748344 0.88888889]
 [0.9054326  0.89163347 0.87417219 0.88888889]
 [0.90342052 0.89083665 0.87417219 0.88888889]
 [0.89336016 0.89003984 0.86092715 0.88888889]
 [0.88933602 0.88924303 0.85761589 0.88888889]
 [0.88128773 0.88844622 0.85761589 0.88888889]
 [0.88128773 0.88844622 0.86092715 0.88888889]
 [0.87927565 0.89083665 0.84437086 0.88888889]
 [0.87323944 0.88286853 0.8410596  0.88888889]
 [0.87122736 0.88047809 0.83443709 0.88888889]
 [0.86921529 0.88446215 0.83443709 0.88888889]
 [0.86921529 0.88525896 0.82781457 0.88888889]
 [0.86317907 0.88366534 0.81788079 0.88888889]
 [0.861167   0.88047809 0.81125828 0.88888889]
 [0.85915493 0.88047809 0.80794702 0.88888889]
 [0.85714286 0.87808765 0.79801325 0.88888889]
 [0.85513078 0.86772908 0.78807947 0.88888889]
 [0.85513078 0.86693227 0.7781457  0.88888889]
 [0.85110664 0.86374502 0.76821192 0.88888889]
 [0.83702213 0.86215139 0.7615894  0.88888889]
 [0.82293763 0.85498008 0.74172185 0.88888889]
 [0.81287726 0.84063745 0.72516556 0.88888889]
 [0.8028169  0.84063745 0.71523179 0.88888889]
 [0.78672032 0.83187251 0.68874172 0.88888889]
 [0.77867203 0.81673307 0.67218543 0.88888889]
 [0.76056338 0.80956175 0.65562914 0.88888889]
 [0.75452716 0.79760956 0.62913907 0.88888889]
 [0.73038229 0.78486056 0.58609272 0.87037037]
 [0.71428571 0.76733068 0.49668874 0.86111111]
 [0.64386318 0.73227092 0.38741722 0.86111111]
 [0.5331992  0.65737052 0.20860927 0.84259259]]
[[0.67955801 0.53677303 0.46397466 0.30077519]
 [0.67305062 0.53607781 0.45696401 0.29528158]
 [0.67768595 0.5381984  0.46507937 0.30171073]
 [0.70285714 0.57294943 0.5122807  0.34397163]
 [0.72794663 0.60157241 0.56782946 0.41810345]
 [0.74770642 0.60883198 0.59492386 0.44547564]
 [0.76714514 0.63355049 0.62943072 0.48854962]
 [0.79436153 0.64315238 0.6583991  0.51891892]
 [0.80403701 0.64949608 0.65828571 0.55652174]
 [0.83101045 0.66077537 0.678487   0.59076923]
 [0.86206897 0.66589394 0.70210136 0.65979381]
 [0.87076077 0.67606461 0.71049305 0.67132867]
 [0.88141923 0.68233195 0.72797927 0.69818182]
 [0.88951841 0.68689904 0.73781291 0.71910112]
 [0.90038314 0.69080949 0.73837981 0.73846154]
 [0.90558767 0.69329268 0.74698795 0.74708171]
 [0.91104594 0.69610549 0.75405405 0.76494024]
 [0.91428571 0.70286948 0.75512996 0.78688525]
 [0.9123506  0.70221391 0.75555556 0.78688525]
 [0.91291291 0.70470219 0.74647887 0.78688525]
 [0.9118541  0.70733249 0.74787535 0.79338843]
 [0.91167513 0.71119593 0.75428571 0.79338843]
 [0.90797546 0.71419437 0.75036075 0.80334728]
 [0.90666667 0.71884058 0.75072464 0.80672269]
 [0.90123457 0.72238419 0.75510204 0.82051282]
 [0.90030832 0.72426112 0.76358297 0.81012658]
 [0.90289256 0.73239437 0.76005961 0.82403433]
 [0.89669421 0.72918723 0.76161919 0.82758621]
 [0.89740933 0.73300166 0.75675676 0.82758621]
 [0.9        0.74346952 0.76712329 0.84210526]
 [0.90282132 0.74814815 0.76452599 0.84581498]
 [0.89937107 0.75288527 0.76234568 0.84955752]
 [0.89915966 0.75221239 0.75968992 0.85714286]
 [0.90274841 0.75788752 0.76369327 0.84581498]
 [0.90254237 0.76368676 0.76629571 0.87272727]
 [0.90329437 0.76582278 0.76404494 0.87272727]
 [0.90329437 0.7675485  0.75928918 0.87272727]
 [0.90191898 0.7751162  0.7594108  0.87671233]
 [0.89462366 0.78094551 0.76923077 0.88073394]
 [0.88913043 0.78321168 0.76320273 0.87671233]
 [0.88499452 0.78380386 0.75909879 0.87272727]
 [0.87885463 0.7935314  0.76460177 0.87272727]
 [0.86985539 0.79573171 0.75090253 0.88073394]
 [0.86480447 0.79395817 0.74632353 0.88073394]
 [0.85423729 0.80411555 0.74296435 0.88073394]
 [0.85324232 0.8056338  0.73076923 0.88479263]
 [0.83833718 0.80539657 0.70941884 0.87850467]
 [0.82750583 0.80653266 0.64377682 0.86915888]
 [0.77764277 0.795671   0.55319149 0.87323944]
 [0.69010417 0.76001842 0.3442623  0.8708134 ]]